In [1]:
anthro_data = ['participant_id', 'CID', 'age_at_study', 'ecid_weight_recorded',
               'ecid_height_recorded', 'cid_moissl_fat_free_mass',
               'cid_moissl_fat_free_mass_percent',
               'cid_moissl_fat_mass', 'cid_moissl_fat_mass_percent',
               'ecid_sbp', 'ecid_dbp', 'ecid_bpm', 'bmi']

import pandas as pd

# Define the path to your Excel file
PATH = '/Users/user/Downloads/DellaCorte/XSLX/Merged.xlsx'

# Specify the sheet name within the Excel file
sheet_name = 'Means_By_CID'

# Load the data from the Excel file into a Pandas DataFrame
df = pd.read_excel(PATH, sheet_name)


anthro_df = df[anthro_data]

In [2]:
import pandas as pd

# Define the original weights for each 'CID' value in a dictionary
original_weights = {
    1: 1/8,
    2: 1/8,
    3: 1/4,
    4: 1/2
}

anthro_variables = ['age_at_study', 'ecid_weight_recorded',
               'ecid_height_recorded', 'cid_moissl_fat_free_mass',
               'cid_moissl_fat_free_mass_percent',
               'cid_moissl_fat_mass', 'cid_moissl_fat_mass_percent',
               'ecid_sbp', 'ecid_dbp', 'ecid_bpm', 'bmi']

# Load your Excel data
PATH = '/Users/user/Downloads/DellaCorte/XSLX/Merged.xlsx'
sheet_name = 'Means_By_CID'
df = pd.read_excel(PATH, sheet_name)

# Create the 'anthro_df' DataFrame
anthro_df = df[['participant_id', 'CID'] + anthro_variables]

# Get a list of unique 'participant_id' values
unique_participants = anthro_df['participant_id'].unique()

# Create an empty DataFrame to store the results
result_df = pd.DataFrame(columns=['participant_id'] + ['Weighted Average for ' + col for col in anthro_variables])

# Iterate through each 'participant_id'
for target_participant in unique_participants:
    # Create a copy of the DataFrame to avoid SettingWithCopyWarning for each participant
    anthro_df_copy = anthro_df.copy()
    
    # Get the 'CID' values associated with the 'participant_id'
    valid_cids = anthro_df_copy[(anthro_df_copy['participant_id'] == target_participant) & anthro_df_copy['CID'].notna()]['CID'].unique()
    
    # Initialize a list to store weighted averages for each column of interest
    weighted_averages = [target_participant]
    
    for column in anthro_variables:
        # Calculate the weighted average for the current column and 'participant_id'
        weighted_average = 0
        
        # Check if there are valid 'CID' values
        if len(valid_cids) > 0:
            # Select only data where 'column' is not NaN
            valid_data = anthro_df_copy[
                (anthro_df_copy['participant_id'] == target_participant) & 
                anthro_df_copy[column].notna()
            ]
            
            if not valid_data.empty:
                # Calculate the sum of original weights for the available 'CID' values
                sum_original_weights = sum(original_weights[cid] for cid in valid_data['CID'])
                
                # Calculate the rescaled weights to ensure they add up to 1
                valid_data['rescaled_weight'] = valid_data['CID'].map(original_weights) / sum_original_weights
                
                # Calculate the weighted average for the current column and 'participant_id'
                weighted_average = (valid_data[column] * valid_data['rescaled_weight']).sum()
        
        weighted_averages.append(weighted_average)
    
    # Append the results to the result_df
    result_df = result_df.append(pd.Series(weighted_averages, index=result_df.columns), ignore_index=True)

# Print the resulting DataFrame
print(result_df)

# Save the result as an Excel (.xlsx) file
result_df.to_excel('anthro_weighted_averages.xlsx', index=False)



/var/folders/td/8px6smg12fxf4nw_rf4snx840000gn/T/ipykernel_65480/4167243061.py:59: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  valid_data['rescaled_weight'] = valid_data['CID'].map(original_weights) / sum_original_weights
/var/folders/td/8px6smg12fxf4nw_rf4snx840000gn/T/ipykernel_65480/4167243061.py:59: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  valid_data['rescaled_weight'] = valid_data['CID'].map(original_weights) / sum_original_weights
/var/folders/td/8px6smg12fxf4nw_rf4snx840000gn/T/ipykernel_65480

      participant_id  Weighted Average for age_at_study  \
0              149.0                             23.000   
1              150.0                             63.375   
2              151.0                             49.500   
3              152.0                             46.000   
4              153.0                             44.500   
...              ...                                ...   
1564          1793.0                             36.500   
1565          1794.0                             30.000   
1566          1795.0                             48.500   
1567          1796.0                             47.000   
1568          1797.0                             39.500   

      Weighted Average for ecid_weight_recorded  \
0                                          76.5   
1                                          84.3   
2                                         106.7   
3                                          88.8   
4                                   

In [4]:
(1/8)*(72.33) + (1/8)*(79) + (1/4) * 72 + (1/2) * 75.6666667

74.74958335